# Stock Price Prediction for the 5 Biggest Brazilian Commodity-Base Companies  

<img src='Images/1_opening.jpg' style="width:90%; height:500px">


## 1. Overview
### 1.1. Motivation
The stock price market might seems chaotic at a first glance. There is a lot of information that must be taken into account in order to decide whether to buy or not a stock. Some say that the Fundamental Analysis\[1] is the right way to decide whether or not to buy a stock, and some say that the Technical Analysis\[2].

Based on this lack of convergence about which method should be used, and once that we can find a giant amount of data, a data science project could be a nice fit to predict the behaviour of the prices in the next day. Therefore we could use these predictions to guide the decisions.

Nowadays, besides corona crises, the markets of the USA are on their historic maximum. This fact means that there is not so much place to find a share of business with good profits possibilities. Therefore, when we would like to have a bigger profit, we must take more risk and investments that fit this profile are those in emergent markets, like Brazil, India, China, etc. I’m a chemical engineer from Brazil and to use data science to understand the market behaviour for the next weeks are a topic that interests me a lot and can bring my education, my experience living here and my data science skills together.

As we know, the commodity is an economic good that is often used as input the production of other goods or services. These goods have full or substantial fungibility, that is, they can be treated as equivalent (or nearly) regardless of who produced them. Some examples are coffee, gold ore, iron ore, oil, water, electric power, etc. Brazil is a land that has a commodity-based economy\[3] and to be able to predict the share prices of business that work in some level with commodities, cold be an excellent opportunity for discovering bad and good calls.

Besides that, nowadays there are lots of discussions about a commodity rally in 2021\[4]\[5]\[6]\[7]. That means, understanding the future of these goods and being able the share price of the companies or even the commodity itself like gold or silver, are key points to have success investing in Brazil.

So let’s dive in the Brazilian Stock Prices of commodity-based companies, explore them and predict its prices! 


### 1.2. Problem Statement
As mention above, our interest lay on the future share price of commodity-based companies. It gets even more dramatic with 2021 bringing the potential for a commodity rally. To predict those stock prices are a big prize.
**Based on this, we can define that our problem is to analyse the 5 biggest commodity-based companies in Brazil in order to understand their behaviour and relationships as well to get a deeper understanding about what we are going to predict. Then, an algorithm as well its pipeline will be designed and implemented in order to predict the prices for the future.** 


### 1.3. Data and Inputs  
The data will be gathered using the Yahoo! Finance API. A great tutorial (unfortunately only in Portuguese) can be found in this [medium post](https://medium.com/@rodrigobercinimartins/como-extrair-dados-da-bovespa-sem-gastar-nada-com-python-14a03454a720). The library yahooquery gives us all tools to colect the data as we want.  

We will gather data of the 5 biggest commodity-based companies in Brazil, that are:
- Petrobras (PETR4): largest Brazilian company, Petrobras produces oil;  

- Vale (VALE3): the company is among the largest companies in Brazil, and is the largest producer of iron ore in the world;  

- CSN (CSNA3): it is the largest steel industry in Brazil and Latin America, and one of the largest in the world;  

- JBS (JBSS3): the company is one of the largest producers of animal protein in the world;  

- Suzano (SUZB3): the company is considered the largest producer of eucalyptus pulp of the world;  

The data will be divided into 7 features for each day: lowest, highest, open, closed and adjusted close price, as well as volume and ticker.

### 1.4. General Outline   
       a. Gathering the Data;
       b. Cleaning and Exploration;
              b.1. Checking missing values and a first look at the data;
              b.2. Checking the variation of the data over time with a line graph;
              b.3. Using the Moving Average to get another view of price variation;
              b.4. Visualization of Volumes over time;
              b.5. Daily Return;
              b.6. Risk Analysis;
              b.7. Correlations;
       c. Data Preparation;
              c.1. Train-Test Split;
              c.2. Upload the data to S3;
       d. Model Building;
              d.1. RandomForest Regressor;
              d.2. AWS DeepAR;
              d.3. LSTM Model with Tensor Flow
       e. Results;
       f. Conclusion and Next Steps;      
    




In [356]:
!pip install yahooquery
# !pip install tensorflow

In [357]:
# loading packages and utilities
import numpy as np
import pandas as pd
# import tensorflow as tf
import datetime
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
import os
import json

from plotly.subplots import make_subplots
# from tensorflow import keras
from yahooquery import Ticker
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error

%matplotlib inline

In [358]:
def gather_stocks(company_name_list, start = '2007-01-01', end = datetime.date.today()):
    """get the name of the companies, as well as the start and end date, check if they are with the
    ".SA" ending and create a dataframe.
    """
    def name_check(name):
        if name[-2:] != "SA":
            name = name + ".SA"
        return name
    company_name_list = list(map(name_check, company_name_list))

    df = pd.DataFrame(Ticker(company_name_list).history(start = start, end = end)).reset_index()
    return df


## a. Loading the data through Yahoo API

In order to have something to compare, let's gather also data of two ETFs indexes. By having these two indexes we can say if our portfolio is performing better than a basic index. In other words, we will have a winning condition!
The indexes are:
- IBVV11 that replicates IBOVESPA, the benchmark of the 70 biggest Brazilian companies;   

- SPXI11 that replicates S&P500.  

Both are managed by Itau Bank, the biggest bank of south America and can be gathered using the Yahooquery API!

In [359]:
# listing the companies and gathering the data
stock_list = ["PETR4.SA", "VALE3.SA", "CSNA3.SA", "JBSS3.SA", "SUZB3.SA", "BOVV11.SA", "SPXI11.SA"]
start_date = '2017-01-01' #one year before the comodities rally in Brasil
end_date = datetime.date.today() #today
df = gather_stocks(stock_list, start = start_date, end = end_date)

In [360]:
df.head()

symbol        date    low      volume  close   high   open   adjclose  \
0  PETR4.SA  2017-01-02  14.60   7525700.0  14.66  14.70  14.64  11.054067   
1  PETR4.SA  2017-01-03  14.95  39947800.0  15.50  15.65  14.95  11.687451   
2  PETR4.SA  2017-01-04  15.31  37071700.0  15.50  15.68  15.45  11.687451   
3  PETR4.SA  2017-01-05  15.62  47586300.0  15.75  15.91  15.70  11.875957   
4  PETR4.SA  2017-01-06  15.50  25592000.0  15.66  15.92  15.78  11.808098   

   dividends  
0        0.0  
1        0.0  
2        0.0  
3        0.0  
4        0.0

## b. Cleaning and EDA
Now that we gathered some data, let's start the exploration.

### b.1. Checking missing values and a first look at the data

In [361]:
# checkig for missing values
df.isnull().sum()

symbol       0
date         0
low          0
volume       0
close        0
high         0
open         0
adjclose     0
dividends    0
dtype: int64

In [362]:
# checking the infos of the dataset
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9169 entries, 0 to 9168
Data columns (total 9 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   symbol     9169 non-null   object 
 1   date       9169 non-null   object 
 2   low        9169 non-null   float64
 3   volume     9169 non-null   float64
 4   close      9169 non-null   float64
 5   high       9169 non-null   float64
 6   open       9169 non-null   float64
 7   adjclose   9169 non-null   float64
 8   dividends  9169 non-null   float64
dtypes: float64(7), object(2)
memory usage: 644.8+ KB


In [363]:
df.date.unique().shape

(1310,)

In [364]:
df.symbol.unique()

array(['PETR4.SA', 'VALE3.SA', 'CSNA3.SA', 'JBSS3.SA', 'SUZB3.SA',
       'BOVV11.SA', 'SPXI11.SA'], dtype=object)

There are 3496 instances for each company. As we will work with 5 companies and 2 indexes, there are in total 24479 instances for each of the 7 columns and no missing values.

In [365]:
# Checking the earliest instance for each Stock
for stock in stock_list:
    print(df[df.symbol == stock].date.min(), stock)

2017-01-02 PETR4.SA
2017-01-02 VALE3.SA
2017-01-02 CSNA3.SA
2017-01-02 JBSS3.SA
2017-01-02 SUZB3.SA
2017-01-02 BOVV11.SA
2017-01-02 SPXI11.SA


We can notice that all the 5 stocks that we are interested in, are from 2005 and the latest one is SUZB3 from 2007-05-10. So we have data to start, so our model will start on the same page.  

Another important point is that BOVV11 starts on 2016-07-29 and 2015-01-30. Though the registration starts years later it is not a problem at all, once we will use these two indexes just for comparing with our portfolio of commodity-base companies.

Now let's check some statistcs for the stocks.

In [366]:
for stock in stock_list:
    print(df[df.symbol == stock].describe(), stock, "\n\n\n")

               low        volume        close         high         open  \
count  1310.000000  1.310000e+03  1310.000000  1310.000000  1310.000000   
mean     22.528931  6.273336e+07    22.860450    23.215053    22.886359   
std       5.661524  3.549841e+07     5.725086     5.779645     5.722287   
min      10.850000  0.000000e+00    11.290000    12.010000    11.070000   
25%      17.299999  4.028180e+07    17.537500    18.182500    17.792500   
50%      23.280001  5.527355e+07    23.705000    24.120000    23.724999   
75%      27.217499  7.498025e+07    27.510000    27.850000    27.520000   
max      34.389999  4.902304e+08    34.669998    35.290001    35.259998   

          adjclose    dividends  
count  1310.000000  1310.000000  
mean     18.640735     0.005736  
std       5.773727     0.105394  
min       8.776898     0.000000  
25%      13.645622     0.000000  
50%      19.082423     0.000000  
75%      22.550089     0.000000  
max      34.669998     3.250487   PETR4.SA 



     

Here there are a couple of things that must be noticed. They are:
- Std of the volume is pretty high, meaning that there is pretty much variance. It is valid for all stocks;  

- Min and Max price of AdjClose are also big. It means that their values increased tremendously;  

- Looking at the split column, we can see that only SUZB3 was split along with the timespan we are working with;  

- VALE3 paid the highest dividend in order of 2.407510;  

- With a mean of 0.002434 we can say CSNA3 pays more dividends on average that the other 4 companies.  


Now let's plot some line graphs to observe the variation of the prices over time!

### b.2. Checking the variation of the data over time with a line graph

In [367]:
fig = px.line(df, x = "date", y = "adjclose",
              color = 'symbol',
              title = "Stock Prices over Time",
              width = 1000, height = 600)
fig.show()

This comparison in terms of absolute price is the first step, but it will be easier to compare when we work with scaled values. 
  
For the Forecasting step, we need to scale each stock separately. But for purpose of variance comparison, we can scale all data together.

In [368]:
df.adjclose.values

array([ 11.05406666,  11.68745136,  11.68745136, ..., 224.58000183,
       225.1000061 , 227.25      ])

In [369]:
scaler = MinMaxScaler()
df_adjclose_scaled = df.copy()
df_adjclose_scaled.adjclose = scaler.fit_transform(df.adjclose.values.reshape(-1, 1))

In [370]:
fig = px.line(df_adjclose_scaled, x = "date", 
              y = "adjclose", color = 'symbol', 
              title = "Scaled Stock Prices over Time",
              width = 1000, height = 600)
fig.show()

Looking at both graphs we can infer the following:
- Among the 5 stocks, VALE3 reached the highest price both in 2008 and also now in 2020/2021;  

- A big difference is SUZB3. From 2008 until 2018 the company shows a constant price. It means we can't compare the data before 2018 and it may indicate a failure of registration or even that the company wasn't in the stock market until then;  

- After 2018 SUZB3 shows a strong increase in its value, something from around 19.81 to 74.04, increasing 373.75% in 3 years;  

- For the other 3 Stocks, we can see that they walk around but did not increase their value at all along all these years;   

- Another point to see is these 3 Stocks have today similar prices like 2008 when there was a commodity rally. Though 2020 was atypical because of the corona, we can notice a strong increase in their prices. When we compare 2008 and 2020/2021 we can see similar behaviours;  

- Both indexes increase their values over time but we can clearly notice that S&P500 recovered the prices pre corona and skyrocket to a record level and BOVESPA is still walking around very slowly. **It means, we might be seeing an opportunity in the Brazilian market.**

### b.3. Using the Moving Average to get another view of price variation 

In order to visualize a less noisy behaviour and variations let's use now **moving average.** To do so, we need first generate the moving avg for each stock data and then plot it.

In [371]:
fig = make_subplots(rows = 7, cols = 1,
                    subplot_titles = [f"Comparing {i} with its on moving avg of 10 days." for i in stock_list])

for i in range(1,8):
    
    fig.add_trace(
        go.Scatter(x = df[df.symbol == stock_list[i - 1]].date, 
                   y = df[df.symbol == stock_list[i - 1]].adjclose,
                    mode = 'lines',
                    name = stock_list[i - 1]),
                    row = i, col = 1)

    fig.add_trace(
        go.Scatter(x = df[df.symbol == stock_list[i - 1]].date, 
                   y = df[df.symbol == stock_list[i - 1]].adjclose.rolling(10).mean(),
                    mode = 'lines',
                    name = stock_list[i - 1] + " MM"),
                    row = i, col = 1)

fig.update_layout(width = 1000, height = 3000)
fig.show()

Now we can see the price variation for each stock with less noise. Indeed, without a zoom, it seems that nothing change at all, but plotly give us the possibility of zoom in and when we do it, we notice a much smoother line.  
It is especially good when we are observing a peak between 2008 and 2020/2021.  
   
If you have some knowledge of technical analysis, the MA will also be helpful to identify trends and behaviours. Unfortunately, I don't possess, by now, this set of skills, but luckily we can bypass this lack using the ML models.

### b.4. Visualization of Volumes over time

We must understand the trading volume, the flow, as the market fuel. A large flow, a large volume of trading means that a certain directional movement - bullish, for example - is sustained.

In [372]:
fig = px.line(df, x = "date", y = "volume",
              color = 'symbol',
              title = "Stock Volumes over Time",
              width = 1000, height = 600)
fig.show()

Looking stock by stock, separately, we may conclude the following:
- In descending order of volume we have PETR4, VALE3, CSNA3, JBSS3 and SUZB3;  

- As expected, the ETFs have the lowest volumes;   

- Though the price is increasing, the volumes are also increasing. It might mean that the investors believe that the companies still at interesting prices;   

- Independent of the share and the date that it started, there is an increase in volume. We can also notice that this behaviour got stronger and for 2020 and 2021 there is a visible growth of the volumes. **It may show that there is really a bullish tendency.**


### b.5. Daily Return

Though investing for the long term is usually recommended, it can be fun to measure your daily gains — or not so much fun to measure your daily losses — especially after a particularly good or bad day for the market. So we can define a winning condition (some % of gain) or a stop loss (also in %).



In [373]:
# Creating the Daily Return feature
return_list = []
for stock in stock_list:
    return_list.extend(df[df.symbol == stock].adjclose.pct_change())

df['daily_return'] = np.array(return_list)

In [374]:
fig = px.line(df, x = "date", y = "daily_return",
              color = 'symbol',
              title = "Daily Return over Time",
              width = 1000, height = 600)
fig.show()

Here we can observe the following:
- For PETR4 the most part of the fluctuation was within the range of +- 10%;  

- All the stocks present a strong negative variation in something in March or April. This is the effect of Covid-19;   

- After this time with huge fluctuation, the behaviour got normal (the range that they had before). It shows that though pandemic is a very noise time for investing, the prices didn't experience strong variation after the first days of the crisis;   

- This maintenance of behaviour brings confidence for the long term investor as well as for the day-trading because there is some visibility in the price variation.

### b.6. Risk Analysis   

Now we finally can to state which companies are riskier by using the mean and standard deviation of the daily variation.

In [375]:
daily_return_mean = []
daily_return_std = []
for stock in stock_list:
    daily_return_mean.append(df[df.symbol == stock].daily_return.mean())
    daily_return_std.append(df[df.symbol == stock].daily_return.std())

In [376]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = daily_return_mean,
                  y = daily_return_std,
                  mode = "markers+text",
                  marker = dict(size = 10),
                  text = stock_list,
                  textposition='top center'))


fig.update_layout(width = 1000, height=500,
                  title_text='Risk and Expected return for each company')
fig.update_xaxes(title_text = "Expected Return")
fig.update_yaxes(title_text = "Risk")

fig.show()

Using this graph, we can select and establish some order in which companies bring more return with less risk within. That means we want companies that lay far in the x-axes and have lower values for y-axes. So as we notice, this visualization is very helpful for making decisions. 
Through the graph we can state the following:
- The two index ETFs have low-risk associate and SPXI11 has the most desired profile: lowest risk and the second-highest expected return;  

- PETR4 doesn't seem a good choice at all. High Risk and lowest expected return isn't a good fit for the portfolio;  

- VALE3 was the highest-priced stock in the 2008 rally, it is also the highest 2021, we find it with an interesting position with intermediate values both for expected return and for risk;  

- SUZB3 the second-highest priced stock has both the low expected return and low risk. So it could be a safe paper to have in the portfolio;  

- CSNA3 has also both, the highest expected return and the highest risk. It is still interesting to have in the portfolio, once we want to balance SUZB3.  

- Of these 5 companies we should consider, in a real live portfolio, if we want to keep PETR4 and JBSS3. But as we want to create a portfolio for a possible commodity rally, JBSS3 can be easily considered. The only PETR4 due to its low expected return and high risk haven't an interesting profile for the future.  



### b.7. Correlactions

As all the companies are commodity-based, it might be very interesting to investigate how they are correlated. Let's plot it.

In [377]:
df.head()

symbol        date    low      volume  close   high   open   adjclose  \
0  PETR4.SA  2017-01-02  14.60   7525700.0  14.66  14.70  14.64  11.054067   
1  PETR4.SA  2017-01-03  14.95  39947800.0  15.50  15.65  14.95  11.687451   
2  PETR4.SA  2017-01-04  15.31  37071700.0  15.50  15.68  15.45  11.687451   
3  PETR4.SA  2017-01-05  15.62  47586300.0  15.75  15.91  15.70  11.875957   
4  PETR4.SA  2017-01-06  15.50  25592000.0  15.66  15.92  15.78  11.808098   

   dividends  daily_return  
0        0.0           NaN  
1        0.0      0.057299  
2        0.0      0.000000  
3        0.0      0.016129  
4        0.0     -0.005714

In [378]:
# Creating a dataframe only with the close prices and companiys
df.index = df.date
df_corr = pd.DataFrame(index = df[df.symbol == "PETR4.SA"].date)


for stock in stock_list:
    df_corr = pd.merge(df_corr, df[df.symbol == stock].adjclose, on = "date", how = "left")

df.reset_index(drop = True, inplace = True)
df_corr.columns = stock_list
df_corr 

PETR4.SA   VALE3.SA   CSNA3.SA   JBSS3.SA   SUZB3.SA   BOVV11.SA  \
date                                                                            
2017-01-02  11.054067  17.651821   8.582580   9.726717  19.061960   59.660000   
2017-01-03  11.687451  18.433685   9.025144   9.855832  19.061960   61.889999   
2017-01-04  11.687451  18.102625   8.938210   9.855832  19.061960   61.599998   
2017-01-05  11.875957  18.792923   9.246425   9.830009  19.061960   62.080002   
2017-01-06  11.808098  18.292809   8.914501   9.898871  19.061960   61.680000   
...               ...        ...        ...        ...        ...         ...   
2022-04-01  33.009998  96.959999  26.150000  37.509998  54.209999  122.650002   
2022-04-04  32.700001  97.940002  26.430000  38.000000  54.119999  122.330002   
2022-04-05  32.389999  95.110001  25.750000  37.790001  54.169998  119.599998   
2022-04-06  32.360001  96.550003  25.030001  37.590000  55.340000  118.900002   
2022-04-07  34.040001  97.129997  25.170000  37.599998  54.470001  119.529999   

             SPXI11.SA  
date                    
2017-01-02   74.669998  
2017-01-03   75.010002  
2017-01-04   74.660004  
2017-01-05   74.150002  
2017-01-06   74.150002  
...                ...  
2022-04-01  225.750000  
2022-04-04  224.880005  
2022-04-05  224.580002  
2022-04-06  225.100006  
2022-04-07  227.250000  

[1310 rows x 7 columns]

In [379]:
fig = go.Figure(
    go.Heatmap(x = stock_list, y = stock_list, 
               z = df_corr.corr().values,
               colorscale = 'blues')
    )
fig.update_layout(title = "Companies Ajusted Close Price Correlation",
                  width = 1000, height = 600)
fig.show()


Now let's extract some meaning of this correlations.
- PETR4 and BOVV11 are highly correlated. It is expected because Petrobras is one of the biggest Brazilian companies, so it has a heavyweight on BOVV11;  

- VALE3 and SPXI11 are also pretty correlated (0.88). It is very interesting to see how the Brazilian and American market are connected through iron ore performance;  

- CSNA3 also has an interesting correlation with SPXI11 (0.78). As it is a steel producer, I expected to see a stronger correlation with VALE3, but the value was just about 0.65. It seems that it is more correlated with oil by PETR4 (0.76) than with steel;  

- JBSS3 has its highest correlation with IBOVV11. It shows how Agribusiness play a strong role in the Brazilian economy;  

- SUZB3 is also very correlated with SPXI11. It shows also how this kind of business is dependent on dollar.

Here we finish the exploration part and let's move forward to modelling part!

## c. Data Preparation

**A point that must come to light is: this project aims to improve skills on SageMaker and not to build a prediction for each stock. Hence the use of the algorithms is the same regardless of the stock, I would need to train 5 to 7 models spending SageMaker Resources at a cost of repetitions that don't improve any skill on AWS.   
Therefore, once that we investigated the stocks and saw that VALE3 brings an interesting combination of expected return and risk, for the rest of this project, I will work only with this company.**


###  c.1. Train-Test Split

In the rest of this project, we will a bigger amount of data to train (training set) our model and the last 28 days to test it (test set).

As the main goal is to be able to predict the stock price behaviour for the next 28 days (4 weeks), the point is to decide how far in the past should we look. For a first try, let's work with a start data as 02 January of 2018.  
We will have a little bit more than 3 years of data and will try to predict almost 30 days. This should be enough and it will not imply higher training times, meaning lower costs.

For the convenience of the latter steps, let's scale the adjclose for VALE3 now. So latter we can have better efficiency in the models as well as compare the prices in a relative way, which makes the performance easier to visualize!

In [380]:
scaler = MinMaxScaler()
index = df[df.symbol == "VALE3.SA"].index
df.loc[index, "adjclose"] = scaler.fit_transform(df.loc[index].adjclose.values.reshape(-1, 1))
df.loc[index]

symbol        date        low      volume      close       high  \
1310  VALE3.SA  2017-01-02  25.049999   1118500.0  25.059999  25.490000   
1311  VALE3.SA  2017-01-03  25.400000   5658500.0  26.170000  26.170000   
1312  VALE3.SA  2017-01-04  25.360001   2144400.0  25.700001  26.230000   
1313  VALE3.SA  2017-01-05  25.780001   4031600.0  26.680000  26.900000   
1314  VALE3.SA  2017-01-06  25.860001   4213500.0  25.969999  26.590000   
...        ...         ...        ...         ...        ...        ...   
2615  VALE3.SA  2022-04-01  96.070000  22457700.0  96.959999  97.500000   
2616  VALE3.SA  2022-04-04  96.550003  16914000.0  97.940002  98.250000   
2617  VALE3.SA  2022-04-05  94.820000  25764400.0  95.110001  97.779999   
2618  VALE3.SA  2022-04-06  95.330002  22615800.0  96.550003  96.720001   
2619  VALE3.SA  2022-04-07  95.139999  19946600.0  97.129997  97.690002   

           open  adjclose  dividends  daily_return  
1310  25.280001  0.000000        0.0           NaN  
1311  25.510000  0.009234        0.0      0.044294  
1312  26.059999  0.005324        0.0     -0.017960  
1313  25.980000  0.013476        0.0      0.038132  
1314  26.290001  0.007570        0.0     -0.026612  
...         ...       ...        ...           ...  
2615  96.779999  0.936608        0.0      0.014226  
2616  96.769997  0.948182        0.0      0.010107  
2617  97.360001  0.914760        0.0     -0.028895  
2618  95.330002  0.931766        0.0      0.015140  
2619  95.500000  0.938616        0.0      0.006007  

[1310 rows x 10 columns]

In [381]:
df.shape

(9169, 10)

In [382]:
# Spliting the data into train and test
def split_data(df, company_list, prediction_leght, startdate = '2018-01-02'):
    """
        Receive a dataframe with one company or more, as well as a company list and split the data into train and test 
        by the date given as input for each company.
        
        Inputs:
        - df: a dataframe containing at least timestamps and the target columns
        - company_list: a list of company present in the df. They will be splited and formated
        - prediction length: the number of timestamps that should be separeted as test data
        - start_date: is the start of our dataset. Default is the startdate for BOVV11
        
        Returns:
        2 dictionaries containing the train and test datasets for each company. The datasets contain just
        the date column as well as the adjclose (target) column.
    """
    startdate = datetime.datetime.strptime(startdate, '%Y-%m-%d').date()
    
    train = {}
    test = {} 

    for company in company_list:
        train[company] = df[(df.symbol == company) & (df.date > startdate)][:-prediction_length][["date","open","close","high","low","volume", "adjclose"]]
        test[company] = df[(df.symbol == company) & (df.date > startdate)][-prediction_leght:][["date","open","close","high","low","volume", "adjclose"]]

    return train, test

In [383]:
# Defining the timespan to make it efficient and easier for the future
timespan = 28
prediction_length=timespan

# Spliting the data
train, test = split_data(df, stock_list, prediction_length)

In [384]:
train

{'PETR4.SA':             date       open      close       high        low       volume  \
 255   2018-01-03  16.490000  16.700001  16.719999  16.370001   55940900.0   
 256   2018-01-04  16.780001  16.730000  16.959999  16.620001   37064900.0   
 257   2018-01-05  16.700001  16.830000  16.860001  16.570000   26958200.0   
 258   2018-01-08  16.740000  17.030001  17.030001  16.709999   28400000.0   
 259   2018-01-09  17.030001  17.030001  17.160000  16.959999   35070900.0   
 ...          ...        ...        ...        ...        ...          ...   
 1277  2022-02-18  32.570000  33.000000  33.090000  32.270000   60304700.0   
 1278  2022-02-21  33.049999  33.849998  34.000000  33.000000   51263800.0   
 1279  2022-02-22  34.220001  33.740002  34.680000  33.209999   80206700.0   
 1280  2022-02-23  34.180000  34.220001  34.599998  33.799999   86530100.0   
 1281  2022-02-24  34.799999  33.389999  35.290001  32.680000  139674100.0   
 
        adjclose  
 255   12.592289  
 256   12.61

In [385]:
test

{'PETR4.SA':             date       open      close       high        low       volume  \
 1282  2022-02-25  33.450001  34.000000  34.000000  32.900002   86189100.0   
 1283  2022-03-02  35.259998  34.669998  35.290001  34.389999   58071800.0   
 1284  2022-03-03  34.820000  34.240002  34.930000  34.160000   69237400.0   
 1285  2022-03-04  34.080002  34.230000  34.680000  33.820000   55418000.0   
 1286  2022-03-07  34.500000  31.799999  34.599998  31.629999  110954100.0   
 1287  2022-03-08  32.000000  32.459999  32.970001  31.510000  111633500.0   
 1288  2022-03-09  32.599998  32.560001  32.820000  31.740000   87779300.0   
 1289  2022-03-10  32.599998  33.700001  34.599998  32.520000  136437700.0   
 1290  2022-03-11  33.910000  32.490002  34.380001  32.070000   92153700.0   
 1291  2022-03-14  32.430000  31.870001  32.889999  31.520000   52274100.0   
 1292  2022-03-15  31.139999  31.100000  31.540001  30.469999   66272000.0   
 1293  2022-03-16  31.500000  30.830000  31.540001  

In [386]:
# %cd /content/drive/MyDrive/freelancing_projects/stock price prediction

# Data store in S3

In [387]:
# Saving the train and test data on data folder
for stock in stock_list:
    train[stock].to_csv("./data/train_{}.csv".format(stock[:4].lower()), index = False)
    test[stock].to_csv("./data/test_{}.csv".format(stock[:4].lower()), index = False)

In [388]:
# Importing general aws session configuration
import boto3
import sagemaker
from sagemaker import get_execution_role

session = sagemaker.Session()
role = get_execution_role()

bucket = session.default_bucket()

In [389]:
# Creating specific configuration
prefix = "stock-price-prediction-project"
data_dir = "./data"
paths = {}

# Addressing the data on the disc
train_key = os.path.join(data_dir, "train_{}.csv".format("vale"))
test_key = os.path.join(data_dir, "test_{}.csv".format("vale"))

# Path where the files will be saved
train_prefix = "{}/{}".format(prefix, "train_{}".format("vale"))
test_prefix = "{}/{}".format(prefix, "test_{}".format("vale"))

# Uploading to S3
paths["train"] = session.upload_data(train_key, bucket = bucket, key_prefix = train_prefix)
paths["test"] = session.upload_data(test_key, bucket = bucket, key_prefix = test_prefix)

In [390]:
paths["train"]

's3://sagemaker-us-east-1-076039889373/stock-price-prediction-project/train_vale/train_vale.csv'

In [391]:
paths["test"]

's3://sagemaker-us-east-1-076039889373/stock-price-prediction-project/test_vale/test_vale.csv'

# Model Building

In [392]:
from sklearn.ensemble import RandomForestRegressor

In [393]:
# Let's concatanete the train and test dataframes to do just one feature engineering process
df_rf = pd.concat([train["VALE3.SA"], test["VALE3.SA"]])
df_rf.index = df_rf.date
df_rf = df_rf.drop("date", axis = 1)
df_rf.head()

open      close       high        low      volume  adjclose
date                                                                        
2018-01-03  41.830002  41.470001  41.880001  41.299999  12744200.0  0.151824
2018-01-04  41.810001  41.639999  42.369999  41.520000  18433000.0  0.153301
2018-01-05  41.570000  42.290001  42.290001  41.310001  15251300.0  0.158948
2018-01-08  42.400002  43.230000  43.230000  42.400002  14542800.0  0.167115
2018-01-09  43.580002  43.070000  43.750000  42.930000  15986200.0  0.165725

In [394]:
X_train_rf = df_rf.iloc[:-timespan].drop("adjclose", axis = 1)
y_train_rf = df_rf.iloc[:-timespan].adjclose

X_test_rf = df_rf.iloc[-timespan:].drop("adjclose", axis = 1)
y_test_rf = df_rf.iloc[-timespan:].adjclose

In [395]:
# from sklearn.preprocessing import LabelEncoder
# y_train_trans = LabelEncoder().fit_transform(y_train_rf.astype('float64'))
# y_test_trans= LabelEncoder().fit_transform(y_test_rf.astype('float64'))

In [396]:
# Checking
X_train_rf.shape, X_test_rf.shape, y_train_rf.shape, y_test_rf.shape

((1027, 5), (28, 5), (1027,), (28,))

In [397]:
# Instanciating a Regressor and Training
regressor_rf = RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=1500, n_jobs=None, oob_score=False,
                      random_state=None, verbose=0, warm_start=False)

# Training
regressor_rf.fit(X_train_rf, y_train_rf)

RandomForestRegressor(n_estimators=1500)

In [398]:
prediction_rf = regressor_rf.predict(X_test_trans)

In [399]:
prediction_rf = scaler.inverse_transform(prediction_rf.reshape(1, -1))
y_test_rf = scaler.inverse_transform(y_test_rf.values.reshape(1, -1))

In [400]:
# RMSE
np.sqrt(mean_squared_error(y_test_rf, prediction_rf))


68.32288660497771

In [401]:
# MAE
mean_absolute_error(y_test_rf, prediction_rf)

68.27085585639585

In [402]:
trace1 = go.Scatter(x = X_test_rf.index, y = y_test_rf[0],
                   mode = 'lines',
                   name = 'Real Price')

trace2 = go.Scatter(x = X_test_rf.index, y = prediction_rf[0],
                    mode = "lines",
                    name = "Predicted Price")

layout = go.Layout(title = "Real Price vs Predicted Price using Random Forest Regressor",
                   width = 1000, height = 600)

fig = go.Figure(data = [trace1, trace2], layout = layout)
fig.show()

# Convert to JSON
According to the DeepAR documentation, DeepAR expects to see input training data in a JSON format, with the following fields:

start: A string that defines the starting date of the time series, with the format 'YYYY-MM-DD HH:MM:SS'.
target: An array of numerical values that represent the time series.
cat (optional): A numerical array of categorical features that can be used to encode the groups that the record belongs to. This is useful for finding models per class of item, such as in retail sales, where you might have {'shoes', 'jackets', 'pants'} encoded as categories {0, 1, 2}.

In [403]:
# Converting the data
def convert_to_json(df):
    '''Returns a dictionary of values in DeepAR, JSON format.
       :param ts: A single time series.
       :return: A dictionary of values with "start" and "target" keys.
       '''
    # get start time and target from the time series, ts
    json_obj = {"start": str(df.date.min().strftime("%Y-%m-%d") + " 00:00:00"), 
                "target": list(df.adjclose)}
    return json_obj

In [404]:
# Now let's save the data for VALE3 localy so we can upload it to S3.
def save_json_dataset(df, filename):
    with open(filename, 'wb') as f:
        # for each of our times series, there is one JSON line
        #for ts in df:
        json_line = json.dumps(convert_to_json(df)) + '\n'
        json_line = json_line.encode('utf-8')
        f.write(json_line)
    print(filename + ' saved.')

In [405]:
save_json_dataset(train["VALE3.SA"], "./data/train_vale.json")
save_json_dataset(test["VALE3.SA"], "./data/test_vale.json")

./data/train_vale.json saved.
./data/test_vale.json saved.


In [406]:
train_json_key = os.path.join(data_dir, "train_vale.json")
test_json_key = os.path.join(data_dir, "test_vale.json")

train_json_prefix = "{}/{}".format(prefix, "train_vale_json")
test_json_prefix = "{}/{}".format(prefix, "test_vale_json")

path_train_vale_json = session.upload_data(train_json_key, 
                                           bucket = bucket, 
                                           key_prefix = train_json_prefix)

path_test_vale_json = session.upload_data(test_json_key, 
                                          bucket = bucket, 
                                          key_prefix = test_json_prefix)

In [407]:
# Getting the image uri that points to the DeepAR container for this region.
from sagemaker import image_uris

deepar_image = image_uris.retrieve("forecasting-deepar", region = boto3.Session().region_name)

In [417]:
# Setting up the output path
output_path = "s3://{}/{}/output".format(bucket, prefix)

# Instatiating the model
regressor_deepar = sagemaker.estimator.Estimator(image_uri = deepar_image,
                                                 role = role,
                                                 instance_count = 1,
                                                 instance_type = "ml.m5.xlarge",
                                                 output_path = output_path,
                                                 sagemaker_session = session)

In [421]:
# Hyperparamenters
freq = 'D'
prediction_length = timespan # Four weeks
context_length = train["VALE3.SA"].shape[0] - prediction_length

hyperparameters = {
    "epochs": str(5),
    "time_freq": freq,
    "prediction_length": str(prediction_length),
    "context_length": str(context_length),
    "num_cells": "50",
    "num_layers": "2",
    "mini_batch_size": "128",
    "learning_rate": "0.001",
    "early_stopping_patience": "10"
}

In [422]:
regressor_deepar.set_hyperparameters(**hyperparameters)

In [423]:
%%time
# train and test channels
data_channels = {
    "train": path_train_vale_json,
    "test": path_test_vale_json}

# fit the estimator
regressor_deepar.fit(inputs=data_channels)

2022-04-08 22:38:53 Starting - Starting the training job...
2022-04-08 22:39:16 Starting - Preparing the instances for trainingProfilerReport-1649457533: InProgress
.........
2022-04-08 22:40:46 Downloading - Downloading input data
2022-04-08 22:40:46 Training - Downloading the training image......
2022-04-08 22:41:47 Training - Training image download completed. Training in progress..Arguments: train
[04/08/2022 22:41:52 INFO 140635398018688 integration.py:592] worker started
[04/08/2022 22:41:52 INFO 140635398018688] Reading default configuration from /opt/amazon/lib/python3.6/site-packages/algorithm/resources/default-input.json: {'_kvstore': 'auto', '_num_gpus': 'auto', '_num_kv_servers': 'auto', '_tuning_objective_metric': '', 'cardinality': 'auto', 'dropout_rate': '0.10', 'early_stopping_patience': '', 'embedding_dimension': '10', 'learning_rate': '0.001', 'likelihood': 'student-t', 'mini_batch_size': '128', 'num_cells': '40', 'num_dynamic_feat': 'auto', 'num_eval_samples': '100',

# Deploy and Create a Predictor
Now that we have trained a model, we can use it to perform predictions by deploying it to a predictor endpoint.

In [425]:
%%time

from sagemaker.serializers import JSONSerializer
from sagemaker.deserializers import JSONDeserializer


# create a predictor
predictor_deepar = regressor_deepar.deploy(
    initial_instance_count=1,
    instance_type="ml.t2.large",
    serializer=JSONSerializer(),
    deserializer= JSONDeserializer()
)

---------!CPU times: user 157 ms, sys: 611 µs, total: 158 ms
Wall time: 4min 31s


In [426]:
test_json = {
    "instances": [{"start": str(test["VALE3.SA"].date.values[0]) + " 00:00:00",
                  "target": []}],
    "configuration": {
        "num_samples":50,
        "output_types": ["mean"]
    }}

In [427]:
prediction_deepar = predictor_deepar.predict(test_json)

In [428]:
# Rescaling the restul
prediction_deepar = scaler.inverse_transform(np.array(prediction_deepar["predictions"][0]["mean"]).reshape(1,-1))

In [429]:
# RMSE
np.sqrt(mean_squared_error(y_test_rf, prediction_deepar))

65.43140527563209

In [430]:
# MAE
mean_absolute_error(y_test_rf, prediction_deepar)

65.33927692535298

In [431]:
prediction_deepar[0]

array([22.93789293, 26.46232889, 23.92378978, 27.61459231, 26.06443732,
       28.06530283, 28.9772584 , 29.35979927, 29.7314006 , 31.44554531,
       30.65897308, 29.97354813, 30.69711892, 31.48079412, 31.88460969,
       32.21066618, 32.0183409 , 31.42655693, 31.71620757, 31.18017996,
       31.42015219, 32.1578548 , 32.29932949, 31.4571864 , 33.27211119,
       32.49393731, 32.77967268, 33.12953372])

In [432]:
trace1 = go.Scatter(x = X_test_rf.index, y = y_test_rf[0],
                   mode = 'lines',
                   name = 'Real Price')

trace2 = go.Scatter(x = X_test_rf.index, y = prediction_deepar[0],
                    mode = "lines",
                    name = "Predicted Price")

layout = go.Layout(title = "Real Price vs Predicted Price using AWS DeepAR-Forecasting ",
                   width = 1000, height = 600)

fig = go.Figure(data = [trace1, trace2], layout = layout)
fig.show()

# Results

In [433]:
import pandas as pd
metrics = {"RMSE": [68.322, 65.431], "MAE": [68.270, 65.339]}
pd.DataFrame(metrics, index = ["Random Forest", "DeepAR"] )

RMSE     MAE
Random Forest  68.322  68.270
DeepAR         65.431  65.339

# Deleting The Endpoints

In [440]:
sagemaker.Session().delete_endpoint(predictor_deepar.endpoint)
bucket_to_delete = boto3.resource('s3').Bucket(bucket)
bucket_to_delete.objects.all().delete()